In [1]:
#determining os path for the projecdt directory 
import os
from os.path import exists, join, expanduser

project_name = "tts"
if not exists(project_name):
  ! git clone --quiet https://github.com/tugstugi/{project_name}
  ! cd {project_name} && pip install -q -r requirements.txt

     |████████████████████████████████| 122kB 8.6MB/s 


In [2]:
# wget site directories: the primary intended purpose is to make the corresponding module(s) importable: 
# datasets used for text to audio
# download text2mel
if not exists("ljspeech-text2mel.pth"):
  ! wget -q -O ljspeech-text2mel.pth https://www.dropbox.com/s/4t13ugxzzgnocbj/step-300K.pth

# download SSRN
if not exists("ljspeech-ssrn.pth"):
  ! wget -q -O ljspeech-ssrn.pth https://www.dropbox.com/s/gw4aqrgcvccmg0g/step-100K.pth

In [3]:
#Importing librarie necessary to convert to audio
import sys
sys.path.append(project_name)

import warnings
warnings.filterwarnings("ignore")  # ignore warnings in this notebook

import numpy as np
import torch

from tqdm import *
import IPython
from IPython.display import Audio

from hparams import HParams as hp
from audio import save_to_wav
from models import Text2Mel, SSRN
from datasets.lj_speech import vocab, idx2char, get_test_data

In [8]:
#Conversion of the vocab into the mel spectorgram 
torch.set_grad_enabled(False)
text2mel = Text2Mel(vocab)
text2mel.load_state_dict(torch.load("ljspeech-text2mel.pth").state_dict())
text2mel = text2mel.eval()
ssrn = SSRN()
ssrn.load_state_dict(torch.load("ljspeech-ssrn.pth").state_dict())
ssrn = ssrn.eval()

In [10]:
#Sentences to Synthesize into Audio
SENTENCES = [
    "The birch canoe slid on the smooth planks.",
    "Glue the sheet to the dark blue background.",
    "It's easy to tell the depth of a well.",
    "These days a chicken leg is a rare dish.",
    "Rice is often served in round bowls.",
    "The juice of lemons makes fine punch.",
    "The box was thrown beside the parked truck.",
    "The hogs were fed chopped corn and garbage.",
    "Four hours of steady work faced us.",
    "Large size in stockings is hard to sell.",
    "The boy was there when the sun rose.",
    "A rod is used to catch pink salmon.",
    "The source of the huge river is the clear spring.",
    "Kick the ball straight and follow through.",
    "Help the woman get back to her feet.",
    "A pot of tea helps to pass the evening.",
    "Smoky fires lack flame and heat.",
    "The soft cushion broke the man's fall.",
    "The salt breeze came across from the sea.",
    "The girl at the booth sold fifty bonds."
]

In [11]:
# synthetize by one by one from the above eentences to the audio representations 
for i in range(len(SENTENCES)):
    sentence = SENTENCES[i]
    normalized_sentence = "".join([c if c.lower() in vocab else '' for c in sentence])
    print(normalized_sentence)
    
    sentences = [normalized_sentence]
    max_N = len(normalized_sentence)
    L = torch.from_numpy(get_test_data(sentences, max_N))
    zeros = torch.from_numpy(np.zeros((1, hp.n_mels, 1), np.float32))
    Y = zeros
    A = None

    for t in range(hp.max_T):
      _, Y_t, A = text2mel(L, Y, monotonic_attention=True)
      Y = torch.cat((zeros, Y_t), -1)
      _, attention = torch.max(A[0, :, -1], 0)
      attention = attention.item()
      if L[0, attention] == vocab.index('E'):  # EOS
          break

    _, Z = ssrn(Y)
    
    Z = Z.cpu().detach().numpy()
    save_to_wav(Z[0, :, :].T, '%d.wav' % (i + 1))
    IPython.display.display(Audio('%d.wav' % (i + 1), rate=hp.sr))

The birch canoe slid on the smooth planks.


Glue the sheet to the dark blue background.


It's easy to tell the depth of a well.


These days a chicken leg is a rare dish.


Rice is often served in round bowls.


...

A pot of tea helps to pass the evening.


Smoky fires lack flame and heat.


The soft cushion broke the man's fall.


The salt breeze came across from the sea.


The girl at the booth sold fifty bonds.



Reference to Paper for above implementaion, similar appraoch, original paper had outdated libraries:

Hideyuki Tachibana, Katsuya Uenoyama, Shunsuke Aihara
Efficiently Trainable Text-to-Speech System Based on Deep Convolutional Networks with Guided Attention
https://arxiv.org/abs/1710.08969

Code Reference for above implementation:

https://awesomeopensource.com/project/tugstugi/pytorch-dc-tts


Reference to paper for Topic Representation, libaries outdated was unable to implement using DeepVoice3  

Ping Wei, Peng Kainan, Gibiansky Andrew, Arik Sercan, Kannan, Ajay, Narang Sharan,Raiman Jonathan, Miller John, Deep Voice 3 Scaling Text-To-Speech With Convolutional Sequence Learning Dataset
https://arxiv.org/pdf/1710.07654v3.pdf


Github URL for original code for Paper

https://github.com/r9y9/deepvoice3_pytorch

Datasets:	

https://www.dropbox.com/s/4t13ugxzzgnocbj/step-300K.pth
https://www.dropbox.com/s/gw4aqrgcvccmg0g/step-100K.pth
Both from LJ-Speech-Dataset used in paper, actual link below 
https://keithito.com/LJ-Speech-Dataset/